```
installations

```

In [2]:
# !pip install sshtunnel

## Imported modules

In [3]:
import json
import scrapping
import psycopg2
from psycopg2.extras import execute_batch
import re
import logging
import glob
import threading
import datetime
from sshtunnel import SSHTunnelForwarder
import multiprocessing
import os
from typing import Tuple
logging.basicConfig(
    level=logging.INFO, filename=f'./logs/{datetime.datetime.now().strftime("%Y-%m-%d_%H-%M-%S")}.log', filemode='w',
    format='%(name)s - %(levelname)s - %(asctime)s - %(message)s', datefmt='%d-%b-%y %H:%M:%S')
# from psycopg2.extensions import register_adapter


# Web Scraping for English translations

## Functions

In [4]:
def send_data_to_db(data: list):
    try:
        conn = psycopg2.connect(dbname='dh', user='dh', password='qwerty',
                                host='dh.saret.tk', port='5432', sslmode='require')
        connection = conn.cursor()
        execute_batch(
            connection,
            "insert into raw_texts values (%(id_text)s, %(project_name)s, %(raw_text)s) ON CONFLICT DO NOTHING", data)
        conn.commit()
    except Exception as e:
        logging.error(f"Error in {data}:{e}")


def run_file():
    pass


def get_project_files(project_name: str) -> list:
    return glob.glob(f'jsons_unzipped/{project_name}/**/corpusjson/*.json', recursive=True) + glob.glob(
        f'jsons_unzipped/{project_name}/corpusjson/*.json', recursive=True)


def download_text(filepath: str,  oracc_site: str = 'oracc.museum.upenn.edu') -> None:
    cur_json = scrapping._load_json_from_path(filepath)
    try:
        project_name = cur_json['project']
    except UnboundLocalError:
        logging.error(f"Empty file: {filepath}")
        return None
    except TypeError:
        logging.error(f"Error in {filepath}")
        return None
    url = f"http://{oracc_site}/{project_name}/{cur_json['textid']}/html"
    send_data_to_db([{"id_text": cur_json['textid'],
                      "project_name": project_name,
                      "raw_text": scrapping._clean_raw_text(scrapping._download_data_from_website(url))}])


def run_this_shit(project: str) -> None:
    for file in get_project_files(project):
        theadme = threading.Thread(None, download_text, args=(file,))
        try:
            theadme.start()
        except Exception as e:
            logging.error(e)


def run_this_other_shit() -> None:
    conn = psycopg2.connect(dbname='dh', user='dh', password='qwerty',
                            host='dh.saret.tk', port='5432', sslmode='require')
    connection = conn.cursor()
    connection.execute('select distinct(project_name) from raw_texts')
    # project_lists = [p[0] for p in connection.fetchall()]
    # connection.close()
    for project in connection.fetchall():
        for file in get_project_files(project[0]):
            theadme = threading.Thread(None, download_text, args=(file,))
            try:
                theadme.start()
            except Exception as e:
                logging.error(f'{e}: {e.args}')


def create_missing_list():
    conn = psycopg2.connect(dbname='dh', user='dh', password='qwerty',
                            host='dh.saret.tk', port='5432', sslmode='require')
    connection = conn.cursor()
    with open("project_list") as file:
        files = "\n".join(['\n'.join(get_project_files(project[:-1])) for project in file.readlines()])
    with open("missing_list.txt", "w") as missing_list:
        connection.execute('select id_text from raw_texts')
        ids = [nod[0] for nod in connection.fetchall()]
        for _id in ids:
            files = re.sub(f'jsons_unz.+{_id}.+\n+', '', files)
            logging.info(files.count('n\n'))
        missing_list.write(files)


# grab grammatical transliteration

In [5]:
def connect_to_database(
        database: str, user: str = None, password: str = None, host: str = None, port: int = None, sslmode: str=None) -> Tuple[
        psycopg2.extensions.connection, psycopg2.extensions.cursor]:
    if user is not None and password is not None and host is not None and port is not None and sslmode is not None:
        conn = psycopg2.connect(f"dbname='{database}' user='{user}' host='{host}' password='{password}' port='{port}' sslmode='{sslmode}'")
        return conn, conn.cursor()
    try:
        conn = psycopg2.connect(database)
        return conn, conn.cursor()
    except Exception as e:
        logging.error(e)
        return None, None


def get_grammatical_transliteration_from_json() -> None:
    try:
        conn, connection = connect_to_database(dbname='dh', user='dh', password='qwerty', host='dh.saret.tk', port='5432', sslmode='require')
        connection.execute("select project from projects")
        for project in connection.fetchall():
            data_project = scrapping.get_raw_akk_texts_of_project(project[0])
            execute_batch(
                connection,
                'update raw_texts set transliteration=%(raw_text)s where id_text like %(id_text)s',
                data_project)
            conn.commit()
    except Exception as e:
        logging.error(f'{e}: {e.args}')

def get_grammatical_transliteration_from_json_of_all_data() -> None:
    conn, connection = connect_to_database(dbname='dh', user='dh', password='qwerty', host='dh.saret.tk', port='5432', sslmode='require')
    connection.execute("select project from projects")
    for project in connection.fetchall():
        try:
            data_project = scrapping.get_raw_akk_texts_of_project(project[0])
            execute_batch(connection, 'insert into new values (%(id_text)s, %(raw_text)s) on conflict do nothing', data_project)
            conn.commit()
        except Exception as e:
            logging.error(f'{e}: {e.args}')


In [5]:
# get_grammatical_transliteration_from_json()
get_grammatical_transliteration_from_json_of_all_data()

In file jsons_unzipped/adsd\adart1\corpusjson\X103280.json failed because of 'NoneType' object is not subscriptable
In file jsons_unzipped/adsd\adart2\corpusjson\X201680.json failed because of 'NoneType' object is not subscriptable
In file jsons_unzipped/ario\corpusjson\Q007131.json failed because of 'NoneType' object is not subscriptable
In file jsons_unzipped/ario\corpusjson\Q007189.json failed because of 'NoneType' object is not subscriptable
In file jsons_unzipped/atae\guzana\corpusjson\X214098.json failed because of 'cdl'
In file jsons_unzipped/atae\guzana\corpusjson\X214099.json failed because of 'cdl'
In file jsons_unzipped/atae\guzana\corpusjson\X214100.json failed because of 'cdl'
In file jsons_unzipped/atae\mallanate\corpusjson\X217065.json failed because of 'cdl'
In file jsons_unzipped/atae\marqasu\corpusjson\P522581.json failed because of 'cdl'
In file jsons_unzipped/atae\marqasu\corpusjson\P522591.json failed because of 'cdl'
In file jsons_unzipped/atae\tilbarsip\corpusjso

# Metadata grab

In [ ]:
def 

# Legacy and experimental

In [4]:
def run_this_other_shit() -> None:
    with open('missing_list.txt') as list:
        for file in list.readlines():
            download_text(file[:-1])

In [29]:
conn = psycopg2.connect(dbname='dh', user='dh', password='qwerty',                                 host='dh.saret.tk', port='5432', sslmode='require')
connection = conn.cursor()
with open('project_list') as f:
    for project in f.read().split('\n'):
        # connection = connection.execute("insert into raw_texts values (%(id_text)s, %(project_name)s, %(raw_text)s)", scrap)
        try:
            scrap = scrapping.get_raw_english_texts_of_project(project)
        except Exception:
            logging.error(f"Error in {project}:{Exception}")
        try:
            execute_batch(
                connection,
                "insert into raw_texts values (%(id_text)s, %(project_name)s, %(raw_text)s) ON CONFLICT DO NOTHING",
                scrap)
            conn.commit()
        except Exception:
            with open(project, 'w') as f:
                f.write(json.dumps(scrap))
            logging.error(f"Error in {project}:{Exception}")

In [3]:
conn = psycopg2.connect(dbname='dh', user='dh', password='qwerty',                                 host='dh.saret.tk', port='5432', sslmode='require')
connection = conn.cursor()
logging.basicConfig(
    level=logging.INFO, filename=f'./now.log',
    format='%(name)s - %(levelname)s - %(message)s')
logging.info('Start')
with open('project_list', encoding='unicode-escape') as f:
    # project = f.read().split('\n')[2]
    for project in f.read().split('\n'):
        # connection = connection.execute("insert into raw_texts values (%(id_text)s, %(project_name)s, %(raw_text)s)", scrap)
        if os.path.exists(project):
            with open(project) as f:
                logging.info(f'reading {project}')
                scrap = json.loads(f.read())
            # scrap = json.loads(project)
                execute_batch(
                    connection, "insert into raw_texts values (%(id_text)s, %(project_name)s, %(raw_text)s) ON CONFLICT DO NOTHING",
                    scrap)
                conn.commit()


In [ ]:
# with open('cams') as file:
conn = psycopg2.connect(dbname='dh', user='dh', password='qwerty',                                 host='dh.saret.tk', port='5432', sslmode='require')
connection = conn.cursor()
scrap = scrapping.get_raw_english_texts_of_project('saao')
execute_batch(
    connection, "insert into raw_texts values (%(id_text)s, %(project_name)s, %(raw_text)s) ON CONFLICT DO NOTHING",
    scrap)
conn.commit()


In [6]:
with open('project_list') as file:
    for project in file.readlines():
        run_this_shit(project[:-1])
# download_text(r"C:\Users\Saret\Neutral Folder\dh\saao\saa03\corpusjson\P336604.json")


Exception in thread Thread-6843:
Traceback (most recent call last):
  File "c:\Users\Saret\Programming\C#\DH\venv\lib\site-packages\urllib3\connection.py", line 174, in _new_conn
Exception in thread Thread-6825:
Traceback (most recent call last):
  File "c:\Users\Saret\Programming\C#\DH\venv\lib\site-packages\urllib3\connection.py", line 174, in _new_conn
Exception in thread Thread-6877:
Traceback (most recent call last):
  File "c:\Users\Saret\Programming\C#\DH\venv\lib\site-packages\urllib3\connection.py", line 174, in _new_conn
    conn = connection.create_connection(
  File "c:\Users\Saret\Programming\C#\DH\venv\lib\site-packages\urllib3\util\connection.py", line 95, in create_connection
Exception in thread Thread-6889:
Traceback (most recent call last):
  File "c:\Users\Saret\Programming\C#\DH\venv\lib\site-packages\urllib3\connection.py", line 174, in _new_conn
    conn = connection.create_connection(
  File "c:\Users\Saret\Programming\C#\DH\venv\lib\site-packages\urllib3\util\co

In [5]:
create_missing_list()

In [4]:
run_this_other_shit()